# Week 1 Challenge Project
### Lyle Lalunio
---
Hypothyroidism, also called underactive thyroid or low thyroid, is a disorder of the endocrine system in which the thyroid gland does not produce enough thyroid hormone. It can cause a number of symptoms, such as poor ability to tolerate cold, a feeling of tiredness, constipation, depression, and weight gain. Occasionally there may be swelling of the front part of the neck due to goitre. Untreated hypothyroidism during pregnancy can lead to delays in growth and intellectual development in the baby or cretinism.

Worldwide, too little iodine in the diet is the most common cause of hypothyroidism. In countries with enough iodine in the diet, the most common cause of hypothyroidism is the autoimmune condition Hashimoto's thyroiditis. Less common causes include: previous treatment with radioactive iodine, injury to the hypothalamus or the anterior pituitary gland, certain medications, a lack of a functioning thyroid at birth, or previous thyroid surgery. The diagnosis of hypothyroidism, when suspected, can be confirmed with blood tests measuring thyroid-stimulating hormone (TSH) and thyroxine levels.

Worldwide about one billion people are estimated to be iodine deficient; however, it is unknown how often this results in hypothyroidism. In the United States, hypothyroidism occurs in 0.3–0.4% of people.

And that is why we iodize salt.

![alt text](https://www.mayoclinic.org/-/media/kcms/gbs/patient-consumer/images/2013/11/15/17/39/ds00181_-ds00344_-ds00353_-ds00491_-ds00492_-ds00567_-ds00660_-my00709_im01872_thyroid_gif.jpg)



Background: Doctors all around the world need our help to predict whether a patient has hypothyroid disease. We have already overspent our budget to collect such complete data on about 30 attributes for 2800 patients--a good starting number, but a larger sample would certainly be preferred. Moving forward, however, we simply cannot afford to spend so much money on data collection. Therefore, we also need to determine which attributes are the most meaningful to the predictive models, and cut out the rest that don't contribute much. 

The boss wants to see a **balanced** model that can predict with a **high sensitivity** and **high specificity** while using a ***low amount of features***. Collecting complete data such as this is very rare, very time-consuming, and often very expensive. By minimizing the number of features, it will optimize future data collection by deciding what needs to be collected, and what doesn't.

## Loading the data

Let's read the data into a Pandas dataframe and look at the first 20 records.

In [ ]:
import pandas as po
url = "https://raw.githubusercontent.com/Medlytics2022/Week1/master/Datasets/allhypo.train.data"
dataset = po.read_csv(url) 
# dataset.head(20)

In [ ]:
dataset.columns = ['Age', 'Sex', 'On Thyroxine', 'Query on Thyroxine', 'On Antithyroid Medication', 'Sick', 'Pregnant', 'Thyroid Surgery', 'I131 Treatment', 'Query Hypothyroid', 'Query Hyperthyroid', 'Lithium', 'Goiter', 'Tumor', 'Hypopituitary', 'Psych', 'TSH Measured', 'TSH', 'T3 Measured', 'T3', 'TT4 Measured', 'TT4', 'T4U Measured', 'T4U', 'FTI Measured', 'FTI', 'TBG Measured', 'TBG', 'Referral Source', 'Class']

In [ ]:
### Your code here
# import regular expression package
import re  

# define the regular expression for the ".|####" part of dataset['class']

regex_pattern = ( "\."   # looks for the period...
                  "\|"   # followed by a pipe...
                  "\d+") # followed by one or more digit

for index, row in dataset.iterrows():
    
    # substitute instances of our regex_pattern for an empty string
    new_class = re.sub(regex_pattern, '', row['Class'])
    dataset.loc[index,'Class']=new_class

# print(dataset['Class'] == 'secondary hypothyroid')
# dataset = dataset.drop(rows = dataset.rows[dataset['Class'] == 'secondary hypothyroid'])
dataset = dataset.drop(dataset[dataset['Class'] == 'secondary hypothyroid'].index)

# print(dataset[dataset['Class'] == 'secondary hypothyroid'].)
# dataset.head()


In [ ]:
_deepnote_run_altair(dataset, """{"$schema":"https://vega.github.io/schema/vega-lite/v4.json","mark":{"type":"bar","tooltip":true},"height":220,"autosize":{"type":"fit"},"data":{"name":"placeholder"},"encoding":{"x":{"field":"Class","type":"nominal","sort":null,"scale":{"type":"linear","zero":false}},"y":{"field":"COUNT(*)","type":"quantitative","sort":null,"aggregate":"count","scale":{"type":"linear","zero":true}},"color":{"field":"","type":"nominal","sort":null,"scale":{"type":"linear","zero":false}}}}""")

alt.Chart(...)

Great, looks like the data loaded in properly. Let's continue looking at some summary statistics on our data.

## Viewing summary statistics
The functions describe() and info() are your friends

In [ ]:
# output high-level column statistics
dataset.describe()

Age   Sex On Thyroxine Query on Thyroxine On Antithyroid Medication  \
count   2798  2798         2798               2798                      2798   
unique    94     3            2                  2                         2   
top       59     F            f                  f                         f   
freq      75  1829         2468               2758                      2764   

        Sick Pregnant Thyroid Surgery I131 Treatment Query Hypothyroid  ...  \
count   2798     2798            2798           2798              2798  ...   
unique     2        2               2              2                 2  ...   
top        f        f               f              f                 f  ...   
freq    2688     2757            2759           2750              2636  ...   

       TT4 Measured   TT4 T4U Measured   T4U FTI Measured   FTI TBG Measured  \
count          2798  2798         2798  2798         2798  2798         2798   
unique            2   218            2   139            2   210            1   
top               t     ?            t     ?            t     ?            f   
freq           2614   184         2502   296         2504   294         2798   

         TBG Referral Source     Class  
count   2798            2798      2798  
unique     1               5         3  
top        ?           other  negative  
freq    2798            1630      2580  

[4 rows x 30 columns]

In [ ]:
# output information about the data including the index dtype and column dtypes, non-null values and memory usage
#dataset.info()

Note the data types are all objects--even columns that are obviously numeric like Age. This is because there are "?" values for some of the cells, making pandas interpret these columns as non-null objects (instead of int, for example).

## Data cleaning

To start, let's make all the numerical columns contain the correct type of values and change the data type of those columns to numeric. Let's also replace all those question marks with the median of the respective column.

Hint: To make it easier, first try converting all the "?" to NaN.

In [ ]:
import numpy as np

### your code here
drop_columns = ["TBG", "TBG Measured"]
try:
    dataset=dataset.drop(drop_columns,axis=1)
except:
    print("Can't drop columns {}, they may not exist".format(drop_columns))

Hmm, still looks like the TBG column is unfilled, implying it was empty to begin with. Let's get rid of this column, then (and make sure to get rid of it in your list of numeric columns, too!)

In [ ]:
### Your code here
dataset[dataset=='?'] = np.nan

All right, let's take a look now at the info of *just the numeric columns* in the dataset:

In [ ]:
# identify columns by what time of data they hold
numeric_columns = list(["Age","TSH","T3","TT4","T4U","FTI"])

# categorical columns are everything else (minus 'class')
categorical_columns = list(set(dataset.columns)-set(numeric_columns)-set(['Class']))


# convert numeric columns from strings to numbers
dataset[numeric_columns] = dataset[numeric_columns].apply(po.to_numeric)

# print statement for sanity check
print('Numerical Columns: ', numeric_columns)
print('Categorical Columns: ', categorical_columns)

dataset.head(4)

Numerical Columns:  ['Age', 'TSH', 'T3', 'TT4', 'T4U', 'FTI']
Categorical Columns:  ['Query Hypothyroid', 'Sick', 'On Antithyroid Medication', 'Referral Source', 'T3 Measured', 'TT4 Measured', 'Pregnant', 'Query on Thyroxine', 'I131 Treatment', 'T4U Measured', 'Goiter', 'Thyroid Surgery', 'Hypopituitary', 'FTI Measured', 'Sex', 'Lithium', 'Psych', 'Query Hyperthyroid', 'On Thyroxine', 'TSH Measured', 'Tumor']


Age Sex On Thyroxine Query on Thyroxine On Antithyroid Medication Sick  \
0  41.0   F            f                  f                         f    f   
1  23.0   F            f                  f                         f    f   
2  46.0   M            f                  f                         f    f   
3  70.0   F            t                  f                         f    f   

  Pregnant Thyroid Surgery I131 Treatment Query Hypothyroid  ... T3 Measured  \
0        f               f              f                 f  ...           t   
1        f               f              f                 f  ...           t   
2        f               f              f                 f  ...           f   
3        f               f              f                 f  ...           t   

    T3 TT4 Measured    TT4 T4U Measured   T4U FTI Measured    FTI  \
0  2.5            t  125.0            t  1.14            t  109.0   
1  2.0            t  102.0            f   NaN            f    NaN   
2  NaN            t  109.0            t  0.91            t  120.0   
3  1.9            t  175.0            f   NaN            f    NaN   

  Referral Source     Class  
0            SVHC  negative  
1           other  negative  
2           other  negative  
3           other  negative  

[4 rows x 28 columns]

Perfect, now let's fix that class feature. According to the note the data collectors included with this data, the ".|####" refers to a patient number, and is not necessarily relevant for our purposes here.

In [ ]:
### Your code here
# import regular expression package
import re  

# define the regular expression for the ".|####" part of dataset['class']

regex_pattern = ( "\."   # looks for the period...
                  "\|"   # followed by a pipe...
                  "\d+") # followed by one or more digit

for index, row in dataset.iterrows():
    
    # substitute instances of our regex_pattern for an empty string
    new_class = re.sub(regex_pattern, '', row['Class'])
    dataset.loc[index,'Class']=new_class

dataset.head()

Age Sex On Thyroxine Query on Thyroxine On Antithyroid Medication Sick  \
0  41.0   F            f                  f                         f    f   
1  23.0   F            f                  f                         f    f   
2  46.0   M            f                  f                         f    f   
3  70.0   F            t                  f                         f    f   
4  70.0   F            f                  f                         f    f   

  Pregnant Thyroid Surgery I131 Treatment Query Hypothyroid  ... T3 Measured  \
0        f               f              f                 f  ...           t   
1        f               f              f                 f  ...           t   
2        f               f              f                 f  ...           f   
3        f               f              f                 f  ...           t   
4        f               f              f                 f  ...           t   

    T3 TT4 Measured    TT4 T4U Measured   T4U FTI Measured    FTI  \
0  2.5            t  125.0            t  1.14            t  109.0   
1  2.0            t  102.0            f   NaN            f    NaN   
2  NaN            t  109.0            t  0.91            t  120.0   
3  1.9            t  175.0            f   NaN            f    NaN   
4  1.2            t   61.0            t  0.87            t   70.0   

  Referral Source     Class  
0            SVHC  negative  
1           other  negative  
2           other  negative  
3           other  negative  
4             SVI  negative  

[5 rows x 28 columns]

Let's run the describe() function on just the "class" column.

In [ ]:
dataset['Class'].describe()

count         2798
unique           3
top       negative
freq          2580
Name: Class, dtype: object

It looks like there are actually 4 unique classification variables! Thank goodness we didn't assume it was binary.

Display all the unique values in the class column.

In [ ]:
### Your code here
dataset['Class'].unique()

array(['negative', 'compensated hypothyroid', 'primary hypothyroid'],
      dtype=object)

But let's make it binary for the sake of this example anyway. If you finish early later on, try the multiclass classifier with all 4 values!

In [ ]:
# ### Your code here
# dataset['Class'] = dataset['Class'].replace('negative', 0)                    
# dataset['Class'] = dataset['Class'].replace('compensated hypothyroid', 1)     
# dataset['Class'] = dataset['Class'].replace('primary hypothyroid', 2)         
# dataset['Class'] = dataset['Class'].replace('secondary hypothyroid', 3)

dataset.head(10)

Age Sex On Thyroxine Query on Thyroxine On Antithyroid Medication Sick  \
0  41.0   F            f                  f                         f    f   
1  23.0   F            f                  f                         f    f   
2  46.0   M            f                  f                         f    f   
3  70.0   F            t                  f                         f    f   
4  70.0   F            f                  f                         f    f   
5  18.0   F            t                  f                         f    f   
6  59.0   F            f                  f                         f    f   
7  80.0   F            f                  f                         f    f   
8  66.0   F            f                  f                         f    f   
9  68.0   M            f                  f                         f    f   

  Pregnant Thyroid Surgery I131 Treatment Query Hypothyroid  ... T3 Measured  \
0        f               f              f                 f  ...           t   
1        f               f              f                 f  ...           t   
2        f               f              f                 f  ...           f   
3        f               f              f                 f  ...           t   
4        f               f              f                 f  ...           t   
5        f               f              f                 f  ...           f   
6        f               f              f                 f  ...           f   
7        f               f              f                 f  ...           t   
8        f               f              f                 f  ...           t   
9        f               f              f                 f  ...           t   

    T3 TT4 Measured    TT4 T4U Measured   T4U FTI Measured    FTI  \
0  2.5            t  125.0            t  1.14            t  109.0   
1  2.0            t  102.0            f   NaN            f    NaN   
2  NaN            t  109.0            t  0.91            t  120.0   
3  1.9            t  175.0            f   NaN            f    NaN   
4  1.2            t   61.0            t  0.87            t   70.0   
5  NaN            t  183.0            t  1.30            t  141.0   
6  NaN            t   72.0            t  0.92            t   78.0   
7  0.6            t   80.0            t  0.70            t  115.0   
8  2.2            t  123.0            t  0.93            t  132.0   
9  1.6            t   83.0            t  0.89            t   93.0   

  Referral Source     Class  
0            SVHC  negative  
1           other  negative  
2           other  negative  
3           other  negative  
4             SVI  negative  
5           other  negative  
6           other  negative  
7             SVI  negative  
8             SVI  negative  
9             SVI  negative  

[10 rows x 28 columns]

Before we move on, let's not forget to run the describe() function on just  your categorical columns, too.
Compare it to the describe() that your numeric columns produce.

In [ ]:
for i in categorical_columns:
    print(i, dataset[i].unique())

Query Hypothyroid ['f' 't']
Sick ['f' 't']
On Antithyroid Medication ['f' 't']
Referral Source ['SVHC' 'other' 'SVI' 'STMW' 'SVHD']
T3 Measured ['t' 'f']
TT4 Measured ['t' 'f']
Pregnant ['f' 't']
Query on Thyroxine ['f' 't']
I131 Treatment ['f' 't']
T4U Measured ['t' 'f']
Goiter ['f' 't']
Thyroid Surgery ['f' 't']
Hypopituitary ['f' 't']
FTI Measured ['t' 'f']
Sex ['F' 'M' nan]
Lithium ['f' 't']
Psych ['f' 't']
Query Hyperthyroid ['f' 't']
On Thyroxine ['f' 't']
TSH Measured ['t' 'f']
Tumor ['f' 't']


Great! Let's see if there's any other records we have to address. count() is a nice way to check if we have any other missing values.

In [ ]:
#dataset.count()

We could replace the missing values in proportion to the current number of males and females over the total, but that is making an assumption we don't have to make. For now, let's simply cut the records of all these sexless people out of our data.

In [ ]:
### Your code here
dataset = dataset.dropna(axis='rows')
# dataset = dataset[dataset['Sex'] != np.nan] 
# dataset = dataset.dropna(axis='rows')
dataset.count()

Age                          1946
Sex                          1946
On Thyroxine                 1946
Query on Thyroxine           1946
On Antithyroid Medication    1946
Sick                         1946
Pregnant                     1946
Thyroid Surgery              1946
I131 Treatment               1946
Query Hypothyroid            1946
Query Hyperthyroid           1946
Lithium                      1946
Goiter                       1946
Tumor                        1946
Hypopituitary                1946
Psych                        1946
TSH Measured                 1946
TSH                          1946
T3 Measured                  1946
T3                           1946
TT4 Measured                 1946
TT4                          1946
T4U Measured                 1946
T4U                          1946
FTI Measured                 1946
FTI                          1946
Referral Source              1946
Class                        1946
dtype: int64

Nice! Now we have a pretty clean dataset to work with. Let's now do some further data analysis and visualization to better understand what we're working with.

## Data analysis and visualization

Check the correlation of the dataset

In [ ]:
### Your code here
dataset.corr()

Age       TSH        T3       TT4       T4U       FTI
Age  1.000000 -0.030173 -0.255968 -0.074901 -0.169839  0.030084
TSH -0.030173  1.000000 -0.180465 -0.288480  0.055920 -0.331307
T3  -0.255968 -0.180465  1.000000  0.581544  0.465549  0.346348
TT4 -0.074901 -0.288480  0.581544  1.000000  0.450421  0.786000
T4U -0.169839  0.055920  0.465549  0.450421  1.000000 -0.171435
FTI  0.030084 -0.331307  0.346348  0.786000 -0.171435  1.000000

Convert the class feature to numeric so we can also see the correlations it has with the numeric features, and check the correlation again.

In [ ]:
import pandas as po

### Your code here
dataset["Class"].unique()

array(['negative', 'primary hypothyroid', 'compensated hypothyroid'],
      dtype=object)

In [ ]:
_deepnote_run_altair(dataset, """{"$schema":"https://vega.github.io/schema/vega-lite/v4.json","mark":{"type":"bar","tooltip":true},"height":220,"autosize":{"type":"fit"},"data":{"name":"placeholder"},"encoding":{"x":{"field":"Class","type":"nominal","sort":null,"scale":{"type":"linear","zero":false}},"y":{"field":"COUNT(*)","type":"quantitative","sort":null,"aggregate":"count","scale":{"type":"linear","zero":true}},"color":{"field":"","type":"nominal","sort":null,"scale":{"type":"linear","zero":false}}}}""")

alt.Chart(...)

Let's do some further visual analysis using a new module called seaborn. Explore its incredible versatility and diversity with data visualization here: https://seaborn.pydata.org/

In [ ]:
import seaborn as sns
#sns.pairplot(dataset)

OK! I think we're ready to create and select some supervised learning models. To get the ball rolling, select Age and Sex as our explanatory features (and class as the target feature, obviously).

## Model training and selection

Let's dummy the categorical variables (but not the class value!) and view the column names to select some for our model.

In [ ]:
for i in categorical_columns:
    dataset[i] = dataset[i].replace('t',1)
    dataset[i] = dataset[i].replace('f',0)
    dataset[i] = dataset[i].replace('M',1)
    dataset[i] = dataset[i].replace('F',0)
dataset


Age  Sex  On Thyroxine  Query on Thyroxine  On Antithyroid Medication  \
0     41.0    0             0                   0                          0   
4     70.0    0             0                   0                          0   
7     80.0    0             0                   0                          0   
8     66.0    0             0                   0                          0   
9     68.0    1             0                   0                          0   
...    ...  ...           ...                 ...                        ...   
2788  70.0    1             0                   0                          0   
2790  67.0    1             0                   0                          0   
2793  82.0    0             0                   0                          0   
2794  25.0    0             0                   0                          0   
2799  81.0    0             0                   0                          0   

      Sick  Pregnant  Thyroid Surgery  I131 Treatment  Query Hypothyroid  ...  \
0        0         0                0               0                  0  ...   
4        0         0                0               0                  0  ...   
7        0         0                0               0                  0  ...   
8        0         0                0               0                  0  ...   
9        0         0                0               0                  0  ...   
...    ...       ...              ...             ...                ...  ...   
2788     0         0                0               0                  0  ...   
2790     0         0                0               0                  1  ...   
2793     0         0                0               0                  0  ...   
2794     0         0                0               0                  0  ...   
2799     0         0                0               0                  0  ...   

      T3 Measured   T3  TT4 Measured    TT4  T4U Measured   T4U  FTI Measured  \
0               1  2.5             1  125.0             1  1.14             1   
4               1  1.2             1   61.0             1  0.87             1   
7               1  0.6             1   80.0             1  0.70             1   
8               1  2.2             1  123.0             1  0.93             1   
9               1  1.6             1   83.0             1  0.89             1   
...           ...  ...           ...    ...           ...   ...           ...   
2788            1  1.5             1   70.0             1  0.77             1   
2790            1  2.0             1   83.0             1  0.96             1   
2793            1  1.4             1   74.0             1  0.52             1   
2794            1  1.7             1  167.0             1  1.21             1   
2799            1  1.5             1  114.0             1  0.99             1   

        FTI  Referral Source     Class  
0     109.0             SVHC  negative  
4      70.0              SVI  negative  
7     115.0              SVI  negative  
8     132.0              SVI  negative  
9      93.0              SVI  negative  
...     ...              ...       ...  
2788   91.0              SVI  negative  
2790   87.0              SVI  negative  
2793  143.0            other  negative  
2794  137.0            other  negative  
2799  115.0              SVI  negative  

[1946 rows x 28 columns]

All right, let's now split our data into training and testing in an 80-20 split. For consistency, let's all use a seed of 8675309.

In [ ]:
from sklearn.model_selection import train_test_split


## Your code here
# dataset['Class'] = dataset['Class'].apply(str)
data_train, data_val = train_test_split(dataset, test_size=0.20, random_state=8675309, stratify=dataset['Class'])
# from sklearn.model_selection import ShuffleSplit
# splits = ShuffleSplit(n_splits=5, test_size=0.2, random_state=42)
# data_train, data_val = splits.split()
# print(type(splits))
# x_categories = numeric_columns + categorical_columns
# x_categories = ['Age', 'Sex', 'TSH', 'T3', 'TT4', 'T4U', 'FTI']
x_categories = ['Age', 'TSH', 'T4U']
X_train = data_train[x_categories]
X_val = data_val[x_categories]

y_train = data_train['Class']
y_val = data_val['Class']



In [ ]:
dataset

Age  Sex  On Thyroxine  Query on Thyroxine  On Antithyroid Medication  \
0     41.0    0             0                   0                          0   
4     70.0    0             0                   0                          0   
7     80.0    0             0                   0                          0   
8     66.0    0             0                   0                          0   
9     68.0    1             0                   0                          0   
...    ...  ...           ...                 ...                        ...   
2788  70.0    1             0                   0                          0   
2790  67.0    1             0                   0                          0   
2793  82.0    0             0                   0                          0   
2794  25.0    0             0                   0                          0   
2799  81.0    0             0                   0                          0   

      Sick  Pregnant  Thyroid Surgery  I131 Treatment  Query Hypothyroid  ...  \
0        0         0                0               0                  0  ...   
4        0         0                0               0                  0  ...   
7        0         0                0               0                  0  ...   
8        0         0                0               0                  0  ...   
9        0         0                0               0                  0  ...   
...    ...       ...              ...             ...                ...  ...   
2788     0         0                0               0                  0  ...   
2790     0         0                0               0                  1  ...   
2793     0         0                0               0                  0  ...   
2794     0         0                0               0                  0  ...   
2799     0         0                0               0                  0  ...   

      T3 Measured   T3  TT4 Measured    TT4  T4U Measured   T4U  FTI Measured  \
0               1  2.5             1  125.0             1  1.14             1   
4               1  1.2             1   61.0             1  0.87             1   
7               1  0.6             1   80.0             1  0.70             1   
8               1  2.2             1  123.0             1  0.93             1   
9               1  1.6             1   83.0             1  0.89             1   
...           ...  ...           ...    ...           ...   ...           ...   
2788            1  1.5             1   70.0             1  0.77             1   
2790            1  2.0             1   83.0             1  0.96             1   
2793            1  1.4             1   74.0             1  0.52             1   
2794            1  1.7             1  167.0             1  1.21             1   
2799            1  1.5             1  114.0             1  0.99             1   

        FTI  Referral Source     Class  
0     109.0             SVHC  negative  
4      70.0              SVI  negative  
7     115.0              SVI  negative  
8     132.0              SVI  negative  
9      93.0              SVI  negative  
...     ...              ...       ...  
2788   91.0              SVI  negative  
2790   87.0              SVI  negative  
2793  143.0            other  negative  
2794  137.0            other  negative  
2799  115.0              SVI  negative  

[1946 rows x 28 columns]

In [ ]:
_deepnote_run_altair(dataset, """{"$schema":"https://vega.github.io/schema/vega-lite/v4.json","mark":{"type":"point","tooltip":true},"height":220,"autosize":{"type":"fit"},"data":{"name":"placeholder"},"encoding":{"x":{"field":"Age","type":"quantitative","sort":null,"scale":{"type":"linear","zero":false}},"y":{"field":"COUNT(*)","type":"quantitative","sort":null,"aggregate":"count","scale":{"type":"linear","zero":false}},"color":{"field":"","type":"nominal","sort":null,"scale":{"type":"linear","zero":false}}}}""")

alt.Chart(...)

For reusability, let's make a logistic regression function that will take our training and testing data as arguments. Inside the function, build a model on your training data, fit it with your training class data, and return a list of your predictions.

In [ ]:
from sklearn import metrics
from sklearn.linear_model import LogisticRegression
#from sklearn.metrics import accuracy_score

def log_reg(train_X,train_Y,test_X,test_Y):
    logreg = LogisticRegression()
    model = logreg.fit(train_X, train_Y)
    y_test_pred = model.predict(test_X)
    return y_test_pred
  ### Your code here

Fantastic, we have just built a logistic regression model! Let's go see how well it performs.

### Model evaluation

To start, let's establish the baseline performance. This is important because it provides a starting point of comparison for later evaluation methods, like accuracy.

A good baseline model to use is the Zero Rule algorithm. In classification problems, it simply predicts the class value with the greatest number of instances every time.

In [ ]:
from scipy import stats

def zero_rule_algorithm_classification(train,test):
  ## Your code here
  res = stats.mode(train["Class"])[0][0]
  ret = [res] * len(test)
  return ret

Get your baseline performance by calculating the accuracy of your Zero Rule algorithm.

In [ ]:
## Your code here
from sklearn.metrics import accuracy_score
#print(zero_rule_algorithm_classification(data_train, data_val))
predictions = zero_rule_algorithm_classification(data_train, data_val)
print(accuracy_score(predictions, data_val["Class"]))

0.9205128205128205


So maybe accuracy isn't the best performance measure for this dataset. As you've seen already, even when the models predict "negative" for all the records, we could already achieve a ~92% accuracy. However, that also implies we incorrectly predicted 100% of the positive cases, which in the context of this problem, is fatal.

Thankfully, it isn't the only way to evaluate your model. Let's take a look at a confusion matrix.

![alt text](https://i.imgur.com/uipmEwt.png)

Create a confusion matrix using the logistic regression function you built earlier.

In [ ]:
from sklearn.metrics import confusion_matrix
y_val_proba = log_reg(X_train, y_train, X_val, y_val)
print(confusion_matrix(y_val_proba, y_val))

[[  2   3   1]
 [ 19 355   2]
 [  0   1   7]]
/shared-libs/python3.9/py/lib/python3.9/site-packages/sklearn/linear_model/_logistic.py:444: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(



Yet another appropriate metric is the Area Under the Receiver Operator Curve. Specifically, the diagnostic performance of a test, or the accuracy of a test to discriminate diseased cases from normal cases is evaluated using Receiver Operating Characteristic (ROC) curve analysis.

When you consider the results of a particular test in two populations, one population with a disease, the other population without the disease, you will rarely observe a perfect separation between the two groups. Hence, the overlapping areas in the diagram below (FN, FP).

In a Receiver Operating Characteristic (ROC) curve the true positive rate (Sensitivity) is plotted in function of the false positive rate (100-Specificity) for different cut-off points. Each point on the ROC curve represents a sensitivity/specificity pair corresponding to a particular decision threshold. A test with perfect discrimination (no overlap in the two distributions) has a ROC curve that passes through the upper left corner (100% sensitivity, 100% specificity). Therefore the closer the ROC curve is to the upper left corner, the higher the overall accuracy of the test.

![alt text](https://www.medcalc.org/manual/_help/images/roc_intro1.png)





Now, to graph the AUROC curve, we will need to predict probabilities of choosing a specific class value rather than the class value itself. Make a new logistic regression model that does so.

In [ ]:
from sklearn import metrics
from sklearn.linear_model import LogisticRegression
#from sklearn.metrics import accuracy_score

def log_reg_probs(train_X,train_Y,test_X,test_Y):
    logreg = LogisticRegression()
    model = logreg.fit(train_X, train_Y)
    # print(model.classes_)
    y_test_pred = model.predict_proba(test_X)
    return y_test_pred

Now calculate the area under the receiver operator curve with your predictions.

In [ ]:
from sklearn import metrics
y_val_proba_double = log_reg_probs(X_train, y_train, X_val, y_val)
# fpr, tpr, threshold = metrics.roc_curve(y_val, y_val_proba_double[:,1])
# roc_auc = metrics.auc(fpr, tpr)
# print('AUC: ',roc_auc)

### Your code here

/shared-libs/python3.9/py/lib/python3.9/site-packages/sklearn/linear_model/_logistic.py:444: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(


Now graph the ROC curve using matplotlib, fully labeled.

In [ ]:
# import matplotlib.pyplot as plt
# #titles need to be changed
# plt.title('Receiver Operating Characteristic')
# plt.plot(fpr, tpr, 'b', label = 'AUC = %0.3f' % roc_auc)
# plt.legend(loc = 'lower right')
# plt.plot([0, 1], [0, 1],'r--')
# plt.xlim([0, 1])
# plt.ylim([0, 1])
# plt.ylabel('True Positive Rate')
# plt.xlabel('False Positive Rate')
# plt.show()
# ### Your code here

In conclusion, it looks like this model performed pretty bad. It's probably best to try out different columns or perhaps use a different model before we submit our model for scoring.

# Submitting your Model

Once you believe to have found the best classifier, run your classifier on the test data and make a pickle file containing of your predictions contained a pandas dataframe.

This pandas dataframe will contain three columns for your binary classifier (or 5 columns for the multiclass classifier): the first column should be your model's "best guess" for each patient (either 0 or 1, negative or positive) and the last two columns should be the probability the patient would be classified as either a 0 or 1.

(see below for reference)

In [ ]:
# after running this cell, you should see the pickle file pop up in the file explorer to the left
# use the three dots next to the filename to download the file
# after downloading the pickle file, email it to medlytics-22@mit.edu
import pickle

def column(matrix, i):
    return [row[i] for row in matrix]

# y_val_proba_double = zip(y_val_proba_double
predictions = po.DataFrame({"guesses":y_val_proba,"prob_neg":column(y_val_proba_double, 0),"prob_pos":column(y_val_proba_double, 1)})
prediction_pickle_path = 'prediction_pickle.pkl'

# Create an variable to pickle and open it in write mode
prediction_pickle = open(prediction_pickle_path, 'wb')
pickle.dump(predictions, prediction_pickle)

prediction_pickle.close()

In [ ]:
prediction_unpickle = open(prediction_pickle_path, 'rb')
 
# load the unpickle object into a variable
predictions = pickle.load(prediction_unpickle)
 
print(predictions)

      guesses  prob_neg  prob_pos
0    negative  0.011619  0.986874
1    negative  0.014030  0.984356
2    negative  0.035052  0.960916
3    negative  0.054240  0.938965
4    negative  0.016671  0.981572
..        ...       ...       ...
385  negative  0.019850  0.977860
386  negative  0.015970  0.982375
387  negative  0.042750  0.951343
388  negative  0.029585  0.966758
389  negative  0.019439  0.978512

[390 rows x 3 columns]


# Scoring your Model


**Area Under ROC Curve**: A receiver operating characteristic (ROC) curve plots the true positive rate (y) against the false positive rate (x) at many decision threshold settings (output < threshold = 0, output > threshold = 1). The area under this curve represents the probability that a classifier will rank a randomly chosen positive instance higher than a randomly chosen negative one.

**Confusion Matrix**: You will receive a certain number of points for each correct classification and a certain point penalty for each incorrect classification. The points are weighted, and are designed to equate to 0 in a Zero Rule baseline model. This point scheme is designed to punish you heavily for predicting false positives (FP) and false negatives (FN)--FN cases especially. In doing so, we hope you see the importance of clinical considerations and treat your models from a more human perspective, rather than detached from it.

**Real World Cost**: Similar to the confusion matrix, we want you to keep in mind the other aspects of healthcare analytics--in this case, economic feasibility. In essence, we want you to minimize the amount of time and money spent on data collection by reducing the number of features collected. Each record certainly required a lot of time and money from several individuals and businesses to reliably create, and we hope you gain a better understanding of conducting a useful cost-benefit analysis with this scoring method. The full details of the weighted features can be found in the GitHub.

# Moving to the Next Level

For those that finish early, remember how I converted the class values into simply "negative" and "positive"? Now try tackling the multiclass classifier (predicting the different types of positive hypothyroid cases instead of simply negative or positive)! 

The same rules apply!

<a style='text-decoration:none;line-height:16px;display:flex;color:#5B5B62;padding:10px;justify-content:end;' href='https://deepnote.com?utm_source=created-in-deepnote-cell&projectId=d04d55b4-7bac-4c1b-8ecc-497188aeb017' target="_blank">
 </img>
Created in <span style='font-weight:600;margin-left:4px;'>Deepnote</span></a>